In [1]:
%load_ext autoreload
%autoreload 2

In [2]:
from django.shortcuts import render, HttpResponse
from django.http import JsonResponse
from gaharu.models import Dataset
from django.core.files.base import ContentFile
import base64
from gaharu.libraries.glcm import GLCM
from gaharu.libraries.feature import Morfologi
import uuid
import numpy as np
import cv2
from pprint import pprint
from sklearn.model_selection import StratifiedKFold
from itertools import islice, count
from gaharu.libraries.anfis_pytorch.myanfis import train_hybrid_modified, predict_data_test
import torch
import json
import os
from sklearn.preprocessing import MinMaxScaler
from sklearn.model_selection import train_test_split
os.environ["DJANGO_ALLOW_ASYNC_UNSAFE"] = "true"
import pickle


In [4]:
epoch = 1


data_master =  Dataset.pdobjects.all().to_dataframe()[:100]
columns = ['id', 'form_factor', 'aspect_ratio', 'rect',
       'narrow_factor', 'prd', 'plw', 'idm', 'entropy', 'asm', 'contrast',
       'correlation', 'kelas']
df = data_master.loc[:, columns].copy()
train_df, test_df = train_test_split(df, test_size=0.2, stratify=df.loc[:, ['kelas']], random_state=0)

train_df = train_df.sort_index()
test_df = test_df.sort_index()


train_data = train_df.copy().sort_index()
test_data = test_df.copy().sort_index()

X_train = train_data.loc[:, ~train_data.columns.isin(['id', 'kelas'])]
Y_train = train_data.loc[:, train_data.columns.isin(['kelas'])]
X_test = test_data.loc[:, ~test_data.columns.isin(['id','kelas'])]
Y_test = test_data.loc[:, test_data.columns.isin(['kelas'])]

scaler = MinMaxScaler()
scaler.fit(X_train)

X_train_scaled = scaler.transform(X_train)
X_test_scaled = scaler.transform(X_test)

X_train_scaled_with_class = np.concatenate((X_train_scaled, Y_train.to_numpy()), axis=1)

model = train_hybrid_modified(X_train_scaled_with_class, epoch)

model


### Training for 1 epochs, training size = 80 cases
epoch    0: MSE=0.00000, RMSE=0.00000 =nan%
80 of 80 correct (=100.00%)


AnfisNet(
  Rule  0: IF x0 is mf0 and x1 is mf0 and x2 is mf0 and x3 is mf0 and x4 is mf0 and x5 is mf0 and x6 is mf0 and x7 is mf0 and x8 is mf0 and x9 is mf0 and x10 is mf0
           THEN [[-0.9154782295227051, -0.213911771774292, -0.7572970390319824, -0.5619139671325684, -0.05941629409790039, 0.7265968322753906, -0.972632884979248, -1.1643872261047363, -1.6280139684677124, 2.1720454692840576, 0.5905077457427979, -1.2307376861572266], [-1.2569185495376587, -2.0588104724884033, -0.7818677425384521, -1.2670255899429321, -1.4693013429641724, -1.2477364540100098, 0.15949876606464386, -2.2469112873077393, -0.6969336867332458, -1.8296645879745483, -4.007596492767334, -3.6479618549346924], [0.29848429560661316, -2.004398822784424, 0.9516786336898804, 0.9184049367904663, -0.4347549378871918, -0.9449287056922913, -1.9092458486557007, 3.686013698577881, -0.18648578226566315, -2.7509005069732666, -0.35389140248298645, -0.20143789052963257], [2.2497055530548096, 4.672081470489502, 0.79767036437

In [25]:
Y_test_reshape = Y_test.to_numpy().reshape(-1)
cat_act, cat_pred = predict_data_test(model, X_test_scaled, Y_test_reshape)
print(cat_act)
print(cat_pred)
num_correct = torch.sum(cat_act == cat_pred)
print(num_correct)

tensor([0, 0, 0, 0, 0, 1, 1, 1, 1, 1, 3, 3, 3, 3, 3, 2, 2, 2, 2, 2])
tensor([0, 2, 3, 3, 3, 3, 1, 1, 3, 2, 0, 2, 2, 3, 2, 2, 2, 2, 2, 2])
tensor(9)


In [33]:
Y_test_predicted = cat_pred.cpu().detach().numpy()
json.dumps({'predicted' : Y_test_predicted.tolist()})

'{"predicted": [0, 2, 3, 3, 3, 3, 1, 1, 3, 2, 0, 2, 2, 3, 2, 2, 2, 2, 2, 2]}'

In [37]:
json.loads(train_data.to_json(orient="records"))

[{'id': 113,
  'form_factor': 0.47166,
  'aspect_ratio': 3.05808,
  'rect': 1.29405,
  'narrow_factor': 0.56722,
  'prd': 4.5744,
  'plw': 1.95532,
  'idm': 0.28707,
  'entropy': 6.42842,
  'asm': 0.00247,
  'contrast': 161.03117,
  'correlation': 0.00036,
  'kelas': 0.0},
 {'id': 114,
  'form_factor': 0.55935,
  'aspect_ratio': 2.72122,
  'rect': 1.28144,
  'narrow_factor': 0.60426,
  'prd': 4.20055,
  'plw': 1.85613,
  'idm': 0.29108,
  'entropy': 6.57882,
  'asm': 0.00204,
  'contrast': 149.70665,
  'correlation': 0.00032,
  'kelas': 0.0},
 {'id': 116,
  'form_factor': 0.56863,
  'aspect_ratio': 2.62476,
  'rect': 1.28521,
  'narrow_factor': 0.61436,
  'prd': 4.16617,
  'plw': 1.8534,
  'idm': 0.30337,
  'entropy': 6.51896,
  'asm': 0.00204,
  'contrast': 143.84361,
  'correlation': 0.00029,
  'kelas': 0.0},
 {'id': 117,
  'form_factor': 0.45582,
  'aspect_ratio': 1.78241,
  'rect': 1.5487,
  'narrow_factor': 0.67915,
  'prd': 4.65319,
  'plw': 2.02444,
  'idm': 0.3104,
  'entropy':

In [71]:
test_data['kelas_predicted'] = Y_test_predicted.reshape(-1,1)
test_data = test_data.astype({"kelas": int})
test_data
Y_test.count() / 20 * 100
num_correct.item()
accuracy = float((num_correct / Y_test.count()) * 100) 
accuracy


45.0

In [90]:
train_data_ids = train_data['id'].tolist()
test_data_ids = test_data['id'].tolist()

In [4]:
with open('49e22ac5-6c6e-47fc-b9ff-a1d549e2bbf2', 'rb') as f:
    pickle_data = pickle.load(f)

In [7]:
model_anfis = pickle_data.get('model')

In [8]:
model_anfis

AnfisNet(
  Rule  0: IF x0 is mf0 and x1 is mf0 and x2 is mf0 and x3 is mf0 and x4 is mf0 and x5 is mf0 and x6 is mf0 and x7 is mf0 and x8 is mf0 and x9 is mf0 and x10 is mf0
           THEN [[-1.9247398376464844, -0.42027485370635986, -0.3374302387237549, -0.5374542474746704, 0.45537152886390686, 2.3492021560668945, 0.039628028869628906, -2.52299427986145, -0.9512398838996887, -0.3858869671821594, -1.9654350280761719, -1.3540070056915283], [-1.3411855697631836, 2.3431203365325928, -1.0080108642578125, -4.5732622146606445, -1.2178149223327637, -6.518860816955566, 5.899256706237793, 3.498464822769165, 1.2886168956756592, 4.233470439910889, -12.022037506103516, -3.8013617992401123], [4.19933557510376, 0.16085615754127502, -1.6452258825302124, 3.685753583908081, -0.19565051794052124, 2.643786907196045, -3.404939889907837, 1.9004024267196655, 0.9396980404853821, -0.8009235262870789, 10.668854713439941, 3.847358465194702], [-0.48434850573539734, -1.7956123352050781, 3.1240575313568115, 1.81